In [1]:
import numpy as np
import nltk
from collections import defaultdict
from collections import Counter
from src.classes.database.offer import MongoOffer
from tqdm import tqdm
from enum import Enum
import re
import json

tokenizer = nltk.RegexpTokenizer(r'\w+')

In [2]:
token_list = [tokenizer.tokenize(x.selling) for x in MongoOffer.objects()]
direction = Enum('direction', ['FORWARD', 'BACKWARD', 'SELF'])

In [3]:
def get_all_words(token_list: list[list]) -> list:
    words = []
    for sentence in token_list:
        for word in sentence:
            words.append(word)
    return sorted(set(words))

def next_word_occurrence(key: str, look_ahead: int, tokens: list[list]) -> dict:
    counter = defaultdict(int)
    for sentence in tokens:
        for x in range(0, len(sentence)):
            if key == sentence[x]: #if we find the key in a sentence
                if (x+look_ahead) < len(sentence):
                    counter[sentence[x+look_ahead]] += 1
    return counter

def p_next_word(given: str, looking: str, look_ahead: int, tokens: list[list]) -> float:
    nwo: dict = next_word_occurrence(given, look_ahead, tokens)
    return nwo[looking] / sum(nwo.values()) if nwo[looking] != 0 else 0

# Old method, slow and not used anymore
def calculate_all_probabilities(tokens: list[list], look_ahead) -> dict:
    all_words = get_all_words(tokens)

    #Generating a list of all words
    word_canvas = defaultdict()
    for word in all_words:
        word_canvas[word] = None

    p_word = word_canvas.copy()
    for word in tqdm(p_word):
        p_word[word] = [defaultdict(float) for x in range(0,look_ahead)]
        for x in range(0,look_ahead):
            for sub_word in all_words:
                p = p_next_word(word, sub_word, x+1, tokens)
                if p > 0:
                    p_word[word][x][sub_word] = p_next_word(word, sub_word, x+1, tokens)
                #print(f"{word} | {str(x)} | {sub_word}: {p_word[word][x][sub_word]}")
    return p_word
#data = calculate_all_probabilities(token_list, 1)

## HMaxtrix
Used for storing all word occurrences in a 3 dimensional matrix

### Data we can get from matrix
 1. p(start, find) = probability that 'find' is a n-order forward word for 'start' | single cell value / sum of 'start' row
 2. p(start, find) = probability that 'find' is a n-order backward word for 'start' | single cell value / sum of 'start' column
 3. p(row_word) = probability that 'row word' will be a n-order forward word | sum of row / entire table sum
 4. p(col_word) = probability that 'col word' will be a n-order backward word | sum of column / entire table sum
 5. p(word, order) = probability that 'word' will be n-order word compared to the other orders| single cell value at order / all order values of that word tallied (through the table)
 6.  p(word-row, order) = probability that 'word' will be n-order forward word | all of word-row order sum / all order values of that word-row
 7. p(col-row, order) = probability that 'word' will be n-order backward word | all of word-col order sum / all order values of that word-col

In [4]:
class HMatrix:
    def __init__(self) -> None:
        self.labels = None
        self.reverse_labels = None
        self.order = 0
        self.matrix = None

    def p_row_word(self, order: int, row_word: str, word: str) -> float:
        if row_word not in self.reverse_labels or word not in self.reverse_labels:
            return 0
        row_label = self.reverse_labels[row_word]
        word_label = self.reverse_labels[word]

        dividend = self.matrix[order, row_label, :][word_label]
        divisor = sum(self.matrix[order, row_label, :])

        return dividend/divisor if divisor > 0 else 0

    def p_col_word(self, order: int, col_word: str, word: str) -> float:
        if col_word not in self.reverse_labels or word not in self.reverse_labels:
            return 0
        col_label = self.reverse_labels[col_word]
        word_label = self.reverse_labels[word]

        dividend = self.matrix[order, :, col_label][word_label]
        divisor = sum(self.matrix[order, :, col_label])

        return dividend/divisor if divisor > 0 else 0


    def create_matrix(self, tokens: list[list], order: int):
        #Setup
        self.labels = get_all_words(token_list)
        self.reverse_labels = {self.labels[x]: x for x in range(0, len(self.labels))}
        self.order = order
        self.matrix = np.zeros((order, len(self.labels), len(self.labels)))

        #Iteration
        for sentence in tqdm(tokens):
            for x in range(0, len(sentence)):
                word = sentence[x]
                print(f"Word: {word} ({str(self.reverse_labels[word])})")
                for y in range(0, self.order):
                    if x+y+1 < len(sentence):
                        print(f"Lookahead {str(y+1)}: {sentence[x+y+1]} ({str(self.reverse_labels[sentence[x+y+1]])})")
                        self.matrix[y][self.reverse_labels[word]][self.reverse_labels[sentence[x+y+1]]] += 1

In [5]:
matrix = HMatrix()
matrix.create_matrix(token_list, 8)

 56%|█████▌    | 2361/4244 [00:00<00:00, 12008.01it/s]

Word: logitech (2353)
Lookahead 1: g (1802)
Lookahead 2: pro (2901)
Lookahead 3: x (3878)
Lookahead 4: superlight (3452)
Word: g (1802)
Lookahead 1: pro (2901)
Lookahead 2: x (3878)
Lookahead 3: superlight (3452)
Word: pro (2901)
Lookahead 1: x (3878)
Lookahead 2: superlight (3452)
Word: x (3878)
Lookahead 1: superlight (3452)
Word: superlight (3452)
Word: nintendo (2622)
Lookahead 1: switch (3472)
Lookahead 2: lite (2340)
Lookahead 3: gray (1943)
Lookahead 4: with (3860)
Lookahead 5: original (2717)
Lookahead 6: box (1207)
Lookahead 7: extras (1685)
Lookahead 8: anbernic (1002)
Word: switch (3472)
Lookahead 1: lite (2340)
Lookahead 2: gray (1943)
Lookahead 3: with (3860)
Lookahead 4: original (2717)
Lookahead 5: box (1207)
Lookahead 6: extras (1685)
Lookahead 7: anbernic (1002)
Lookahead 8: rg351p (3066)
Word: lite (2340)
Lookahead 1: gray (1943)
Lookahead 2: with (3860)
Lookahead 3: original (2717)
Lookahead 4: box (1207)
Lookahead 5: extras (1685)
Lookahead 6: anbernic (1002)
Lookah

100%|██████████| 4244/4244 [00:00<00:00, 11847.40it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Sentence Class

Input a sentence, it will then use the HMatrix to see which path results the most likely outcome for products

In [6]:
class Sentence:
    def __init__(self, matrix: HMatrix, tokenizer, raw_sentence: str, verbose=False):
        self.verbose = verbose
        self.raw_sentence = tokenizer.tokenize(raw_sentence.lower())
        self.sentence = []

        # Creating all the blank word classes
        for x, word in enumerate(self.raw_sentence):
            self.sentence.append(Word(word, x))

        # Creating all the forward connections
        for x, word in enumerate(self.raw_sentence):
            if verbose:
                print(f"--- {word} ---")
            for neighbor in self.sentence:
                mapped_pos = self.map_word_pos_to_order(neighbor.position-x)

                if mapped_pos[1] is not direction.SELF and mapped_pos[0] < matrix.order: #Looking at itself and order is within scope
                    p_value = 0

                    if mapped_pos[1] is direction.FORWARD and self.verbose:
                        p_value = matrix.p_row_word(mapped_pos[0], word, neighbor.key)
                    else:
                        p_value = matrix.p_col_word(mapped_pos[0], word, neighbor.key)

                    self.sentence[x].neighbors.append(
                            {'word': neighbor.key,
                             'ref': neighbor,
                             'p': p_value,
                             'direction': mapped_pos[1].name
                            })

                    if verbose:
                        print(f"{'  '*mapped_pos[0]}"
                              f"{word} "
                              f"-{str(mapped_pos[0])}-> "
                              f"{neighbor.key} "
                              f"({str(p_value)})")



    def map_word_pos_to_order(self, position) -> tuple:
        #Forward word positions
        if position > 0:
            return position-1, direction.FORWARD

        # Backwards word positions
        if position < 0:
            return abs(position)-1, direction.BACKWARD

        #Pos looking at self
        if position == 0:
            return -1, direction.SELF



class Word:
    def __init__(self, key: str, position: int):
        self.key = key
        self.position = position
        self.neighbors = []

    # This method will find this word's neighbor by taking the words position + an input position, returns None if out of bounds.
    def get_neighbor(self, pos):
        # Bound Checking
        if pos == 0:
            return None

        if pos+self.position-1 > len(self.neighbors)-1 or pos+self.position < 0:
            return None

        return self.neighbors[pos+self.position-1] if pos > 0 else self.neighbors[pos+self.position]

    def __str__(self):
        return f"Word: {self.key} | Position: {str(self.position)}"


In [7]:
test = Sentence(matrix, tokenizer, "logitech g pro x superlight intel i7 8700k", verbose=True)

--- logitech ---
logitech -0-> g (0.203125)
  logitech -1-> pro (0.21666666666666667)
    logitech -2-> x (0.14035087719298245)
      logitech -3-> superlight (0.09302325581395349)
        logitech -4-> intel (0.0)
          logitech -5-> i7 (0.0)
            logitech -6-> 8700k (0.0)
--- g ---
g -0-> logitech (0.13829787234042554)
g -0-> pro (0.11504424778761062)
  g -1-> x (0.08695652173913043)
    g -2-> superlight (0.046511627906976744)
      g -3-> intel (0.0)
        g -4-> i7 (0.0)
          g -5-> 8700k (0.0)
--- pro ---
  pro -1-> logitech (0.03209876543209877)
pro -0-> g (0.026804123711340205)
pro -0-> x (0.024017467248908297)
  pro -1-> superlight (0.009615384615384616)
    pro -2-> intel (0.008064516129032258)
      pro -3-> i7 (0.0)
        pro -4-> 8700k (0.0)
--- x ---
    x -2-> logitech (0.07920792079207921)
  x -1-> g (0.06722689075630252)
x -0-> pro (0.08270676691729323)
x -0-> superlight (0.03389830508474576)
  x -1-> intel (0.0)
    x -2-> i7 (0.0)
      x -3-> 870

In [13]:
def seperate_products(start_word: Word):
    products = []



# A method to look ahead only 1 word until the next word probability is 0 todo where I left off, this data is breaking, I must make get_neighbor return the same thing, touple?
def traverse_to_first_order_end(word: Word):
    if word.get_neighbor(1) is None:
        return word

    print(f"Start: {word.key}")
    neighbor = word.get_neighbor(1)

    while neighbor['ref'].get_neighbor(1) is not None and neighbor['ref'].get_neighbor(1)['p'] > 0:
        print(f"Visited: {neighbor['word']}({str(neighbor['p'])})")

        # Go to next neighbor
        neighbor = neighbor['ref'].get_neighbor(1)

    if neighbor['ref'].get_neighbor(1) is None:
        print(f"EoS: {neighbor['word']}") # if at end of sentence
    else:
        print(f"EoP: {neighbor['word']}")# if at end of product

In [14]:
test.raw_sentence

['logitech', 'g', 'pro', 'x', 'superlight', 'intel', 'i7', '8700k']

In [15]:
traverse_to_first_order_end(test.sentence[0])

Start: logitech
Visited: g(0.203125)
Visited: pro(0.11504424778761062)
Visited: x(0.024017467248908297)
EoP: superlight


From word a to word b (order 0) there are the following outcomes:
* p(a,b) > 0.0 has 2 outcomes
    * b is part of a
    * b is NOT part of a, but has been seen in the training data
* p(a,b) = 0.0 has 2 outcomes
    * b is NOT part of a
    * b is a new word
        * b is part of a
        * b is part of post b

In [11]:
matrix.p_row_word(0, 'rtx', '5080')

0

I believe the case above where 5080 is a new word, is where we want to look at the word 'rtx' and see what is the probability that it is the final word. If it's close to 0, then we should determine that 5080 is tied to it

In [12]:
test.sentence[0].neighbors

[{'word': 'g',
  'ref': <__main__.Word at 0x11e7cc950>,
  'p': 0.203125,
  'direction': 'FORWARD'},
 {'word': 'pro',
  'ref': <__main__.Word at 0x11e7cd150>,
  'p': 0.21666666666666667,
  'direction': 'FORWARD'},
 {'word': 'x',
  'ref': <__main__.Word at 0x11e7cc9d0>,
  'p': 0.14035087719298245,
  'direction': 'FORWARD'},
 {'word': 'superlight',
  'ref': <__main__.Word at 0x11e7cd210>,
  'p': 0.09302325581395349,
  'direction': 'FORWARD'},
 {'word': 'intel',
  'ref': <__main__.Word at 0x11e7ccb90>,
  'p': 0.0,
  'direction': 'FORWARD'},
 {'word': 'i7',
  'ref': <__main__.Word at 0x11e7ccc50>,
  'p': 0.0,
  'direction': 'FORWARD'},
 {'word': '8700k',
  'ref': <__main__.Word at 0x11e7ccd90>,
  'p': 0.0,
  'direction': 'FORWARD'}]

current thoughts, look at a sentence, for each word choose to point at either right or left, add up all the points and those will be your products